# Import Libraries

In [1]:
import pandas as pd
import matplotlib.pyplot as plt
from bs4 import BeautifulSoup
from sklearn.model_selection import train_test_split
import re
import string
import nltk
from nltk.tokenize import word_tokenize
from nltk.corpus import stopwords
from nltk.stem import PorterStemmer
from nltk.stem import WordNetLemmatizer
lemmatizer = WordNetLemmatizer()
stemmer = PorterStemmer()
import sys
sys.setrecursionlimit(3000)

from sklearn.metrics import recall_score
from sklearn.metrics import precision_score
from sklearn.metrics import f1_score
from sklearn.metrics import hamming_loss
from sklearn.metrics import jaccard_similarity_score

In [2]:
languages = ['vb.net', 'c#', 'c++', '.net']

# Load Datasets

In [3]:
questions = pd.read_csv('stacksample/Questions.csv', encoding = 'latin1')
# answers = pd.read_csv('stacksample/Answers.csv', encoding = 'latin1')
tags = pd.read_csv('stacksample/Tags.csv', encoding = 'latin1')

# Sampling Functions

In [4]:
def sort_by_date(df):
    
    dataframe = df.copy(deep=True)
    sep = 'T'
    print(dataframe)
    for i in range(dataframe.shape[0]):
        head, sep, tail = dataframe.iloc[i]['CreationDate'].partition(sep)
        dataframe.at[i, 'CreationDate'] = head
    
    sorted_dates = dataframe.sort_values(by='CreationDate')
    
    return sorted_dates

In [5]:
def sampling(df):
    
    dataframe = df.copy(deep=True)
    sample = dataframe[(dataframe['CreationDate'] >= '2014-01-01')].reset_index()
    sample = sample.iloc[:,1:]
    
    return sample

# MERGING TWO DATAFRAME

In [6]:
def generate_dataset(df, tag):
    
    data = df.copy(deep=True)
    ta = tag.copy(deep=True)

    ta = ta.astype(str)
    ta = ta.groupby('Id')['Tag'].apply(', '.join).reset_index()
    
    data.Id = data.Id.astype(str)
    ta.Id = ta.Id.astype(str)
    data = pd.merge(data, ta, on='Id')
#     data.to_csv('intermediate_dataset/all_data_questions_with_tags.csv', index=False)

    dataframe = data[['Id', 'Title', 'Body', 'Tag']]
#     dataframe.to_csv('intermediate_dataset/all_questions_only_with_tags.csv', index=False)
    
    return data, dataframe

# TRAIN-TEST SPLIT

In [7]:
def training_testing_split(df):
    
    dataframe = df.copy(deep=True)
    print(dataframe)
    X_train, X_test, y_train, y_test = train_test_split(dataframe[['Id', 'OwnerUserId', 'CreationDate', 'ClosedDate', 'Score', 'Title', 'Body']], dataframe[['Tag']], test_size=0.33, shuffle=False, random_state=0)
    return X_train, X_test, y_train, y_test

# Preprocessing Functions

In [8]:
# Reference: https://stackoverflow.com/questions/43018030/replace-apostrophe-short-words-in-python
def expansion_apostrophes(sentence):

    sentence = re.sub(r"won\'t", "will not", sentence)
    sentence = re.sub(r"can\'t", "can not", sentence)
    sentence = re.sub(r"let\'s", "let us", sentence)
    sentence = re.sub(r"shan\'t", "shall not", sentence)

    sentence = re.sub(r"n\'t", " not", sentence)
    sentence = re.sub(r"\'re", " are", sentence)
    sentence = re.sub(r"\'s", " is", sentence)
    sentence = re.sub(r"\'d", " would", sentence)
    sentence = re.sub(r"\'ll", " will", sentence)
    sentence = re.sub(r"\'t", " not", sentence)
    sentence = re.sub(r"\'ve", " have", sentence)
    sentence = re.sub(r"\'m", " am", sentence)
    
    return sentence

In [9]:
def remove_html_tags(question_body):

    question = BeautifulSoup(question_body, 'html.parser')
    question = question.get_text(separator=" ")
    
    return question

In [10]:
def checknumber(x):
    try:
        float(x)
        return True
    except ValueError:
        return False

In [11]:
def remove_single_letter(str):
    single_list=['c','r'] 
    return(' '.join( [p for p in str.split() if (len(p)>1 or (p in single_list)) ] ))
    

In [12]:
def lowercase(str):
    return(str.lower())

In [13]:
def remove_numbers(str):
    return(' '.join([p for p in str.split() if (not(checknumber(p)))]))

In [14]:
def remove_punctuation(str):
    x=""
    punc=set(string.punctuation)
  
    for word in str.split():
        if word in languages:
            x=x+" "+word
        else:
            x=x+" "+''.join(c for c in word if c not in punc)
    return x


In [15]:
def tokenization(str):
    return(str.split())

In [16]:
def stopwords_removal(str):
    stopWords = set(stopwords.words('english')) 
    stop=[]
    for i in range(len(str)):
        #print(str[i])
        if(str[i] not in stopWords):
            stop.append(str[i])
    return stop

In [17]:
def stemming(str):
    stemmed=[]
   # print(str)
    for i in range(len(str)):
        stemmed.append(lemmatizer.lemmatize(str[i]))
    return stemmed
                    

In [18]:
def remove_numbers_from_list(str):
    notnum=[]
    for i in range(len(str)):
        if not(checknumber(str[i])):
            notnum.append(str[i])
    return notnum

In [19]:
def preprocessing(df):
    
    dataframe = df.copy(deep=True)
    
    for i in range(dataframe.shape[0]):
        
        question = dataframe.iloc[i]['Body']
        title=dataframe.iloc[i]['Title']
        
        # Removing HTML Tags from the question body!
        question = remove_html_tags(question)
        
         # Expansion of apostrophes like won't = will not etc.
        expanded = expansion_apostrophes(question)
        expandedT = expansion_apostrophes(title)
        
        #Case folding
        title=lowercase(expandedT)
        question=lowercase(expanded)
        
       
        #Remove Punctuation
        titlePN=remove_punctuation(title)
        bodyPN=remove_punctuation(question)
       
         
        #Removing single letters
        titleRSL=remove_single_letter(titlePN)
        bodyRSL=remove_single_letter(bodyPN)
        #print(titleRSL)
        
        #Remove numbers
        titleRN=remove_numbers(titleRSL)
        bodyRN=remove_numbers(bodyRSL)
       
        
        #Tokenization
        titletoken=tokenization(titleRN)
        bodytoken=tokenization(bodyRN)
       
        #stopwords removal
        titleSR=stopwords_removal(titletoken)
        bodySR=stopwords_removal(bodytoken)
        #print(titleSR)
        
        #Remove numbers from list after tokenization
        titleRNo=remove_numbers_from_list(titleSR)
        bodyRNo=remove_numbers_from_list(bodySR)
        
        #stemming
        titleSM=stemming(titleRNo)
        bodySM=stemming(bodyRNo)
        #print(titleSM)
        
        titleSM = ' '.join(titleSM)
        bodySM = ' '.join(bodySM)
        
        dataframe.at[i, 'Body'] = bodySM
        dataframe.at[i,'Title'] = titleSM
    return dataframe

In [20]:
def extract_languages(l1, l2, l3, df):
    
    ls = []
    for i in range(df.shape[0]):
        tags = df.iloc[i]['Tag']
        tags = tags.split(",")
        
        if l1 in tags or l2 in tags or l3 in tags:
            ls.append(df.iloc[i])
    return ls
            

In [21]:
def extract_code(code):
    
    codes = []
    soup = BeautifulSoup(code,'html.parser')
    for i in soup.find_all('code'):
        codes.append(str(i))
        i.decompose()
    cd = (''.join(codes))
    return str(soup).encode("utf-8"), cd

In [22]:
def calculate_tfidf_vector(data):
    
    vectorizer_X = TfidfVectorizer(analyzer = 'word', token_pattern=r"(?u)\S\S+", max_features=10000)
    tfidf = vectorizer_X.fit(data)
    X_tfidf = tfidf.transform(data)
    return X_tfidf, tfidf

# Merging the dataframe

In [23]:
dmerged,dfmerged=generate_dataset(questions,tags)

# Sampling Related Function Calls

In [24]:
sorted_dates = sort_by_date(dmerged)

               Id  OwnerUserId          CreationDate            ClosedDate  \
0              80         26.0  2008-08-01T13:57:07Z                   NaN   
1              90         58.0  2008-08-01T14:41:24Z  2012-12-26T03:45:49Z   
2             120         83.0  2008-08-01T15:50:08Z                   NaN   
3             180    2089740.0  2008-08-01T18:42:19Z                   NaN   
4             260         91.0  2008-08-01T23:22:08Z                   NaN   
5             330         63.0  2008-08-02T02:51:36Z                   NaN   
6             470         71.0  2008-08-02T15:11:47Z  2016-03-26T05:23:29Z   
7             580         91.0  2008-08-02T23:30:59Z                   NaN   
8             650        143.0  2008-08-03T11:12:52Z                   NaN   
9             810        233.0  2008-08-03T20:35:01Z                   NaN   
10            930        245.0  2008-08-04T00:47:25Z                   NaN   
11           1010         67.0  2008-08-04T03:59:42Z            

In [25]:
sampled_data = sampling(sorted_dates)
print(sampled_data)

              Id  OwnerUserId CreationDate            ClosedDate  Score  \
0       20871360     991733.0   2014-01-01                   NaN      8   
1       20871350     217408.0   2014-01-01                   NaN      2   
2       20871320      33404.0   2014-01-01                   NaN      0   
3       20871240    2925621.0   2014-01-01                   NaN      0   
4       20871160     362461.0   2014-01-01                   NaN      1   
5       20871030    1924317.0   2014-01-01                   NaN      0   
6       20871080     939870.0   2014-01-01                   NaN      0   
7       20871060     527470.0   2014-01-01                   NaN      2   
8       20871000    2461031.0   2014-01-01                   NaN      1   
9       20870840    1137860.0   2014-01-01                   NaN      0   
10      20870850    2871096.0   2014-01-01                   NaN      0   
11      20871390    3013951.0   2014-01-01                   NaN      1   
12      20870930    31496

In [ ]:
# sampled_data.to_csv("sampled_data.csv", index=False)

# Creating Training Set and Testing Set

In [27]:
X_train, X_test, y_train, y_test = training_testing_split(sampled_data)

              Id  OwnerUserId CreationDate            ClosedDate  Score  \
0       20871360     991733.0   2014-01-01                   NaN      8   
1       20871350     217408.0   2014-01-01                   NaN      2   
2       20871320      33404.0   2014-01-01                   NaN      0   
3       20871240    2925621.0   2014-01-01                   NaN      0   
4       20871160     362461.0   2014-01-01                   NaN      1   
5       20871030    1924317.0   2014-01-01                   NaN      0   
6       20871080     939870.0   2014-01-01                   NaN      0   
7       20871060     527470.0   2014-01-01                   NaN      2   
8       20871000    2461031.0   2014-01-01                   NaN      1   
9       20870840    1137860.0   2014-01-01                   NaN      0   
10      20870850    2871096.0   2014-01-01                   NaN      0   
11      20871390    3013951.0   2014-01-01                   NaN      1   
12      20870930    31496

In [28]:
training_set = pd.concat([X_train, y_train], axis=1)
testing_set = pd.concat([X_test, y_test], axis=1)
print(training_set.shape)
print(testing_set.shape)
training_set.to_csv('intermediate_datasets/training_set.csv', index=False)
testing_set.to_csv('intermediate_datasets/testing_set.csv', index=False)

(441368, 8)
(217391, 8)


In [ ]:
training_tag = training_set[['Id', 'Title', 'Body', 'Tag']]
testing_tag = testing_set[['Id', 'Title', 'Body', 'Tag']]
training_set.to_csv('intermediate_datasets/tags_training.csv', index=False)
testing_set.to_csv('intermediate_datasets/tags_testing.csv', index=False)

# Preprocessing Related Function Calls

In [29]:
dff=preprocessing(training_tag)

NameError: name 'training_tag' is not defined

In [ ]:
dff.to_csv('intermediate_datasets/preprocessed.csv', index=False)

In [30]:
language_data = extract_languages("java", "javascript", "c#", sampled_data)

In [31]:
codes_data = pd.DataFrame(language_data)

In [ ]:
# for i in range(codes_data.shape[0]):
#     extract_code(codes_data.iloc[i][6])

In [ ]:
codes_data.to_csv('intermediate_datasets/java_js_c#_wo_preprocessing_all.csv', index=False)

In [ ]:
codes_data

In [32]:
code_only = codes_data.copy()
tb_only = codes_data.copy()

In [33]:
code_d = codes_data.values

In [34]:
code_body = []
normal_body = []
for i in range(code_d.shape[0]):
    if (i%500)==0:
        print(i)
    codes = extract_code(code_d[i][6])
    code_part = remove_html_tags(codes[1])
    title_body_part = remove_html_tags(codes[0])

    code_body.append(code_part)
    normal_body.append(title_body_part)

0
500
1000
1500
2000
2500
3000
3500
4000
4500
5000
5500
6000
6500
7000
7500
8000
8500
9000
9500
10000
10500
11000
11500
12000
12500
13000
13500
14000
14500
15000
15500
16000
16500
17000
17500
18000
18500
19000
19500
20000
20500
21000
21500
22000
22500
23000
23500
24000
24500
25000
25500
26000
26500
27000
27500
28000
28500
29000
29500
30000
30500
31000
31500
32000
32500
33000
33500
34000
34500
35000
35500
36000
36500
37000
37500
38000
38500
39000
39500
40000
40500
41000
41500
42000
42500
43000
43500
44000
44500
45000
45500
46000
46500
47000
47500
48000
48500
49000
49500
50000
50500
51000
51500
52000
52500
53000
53500
54000
54500
55000
55500
56000
56500
57000
57500
58000
58500
59000
59500
60000
60500
61000
61500
62000
62500
63000
63500
64000
64500
65000
65500
66000
66500
67000
67500
68000
68500
69000
69500
70000
70500
71000
71500
72000
72500
73000
73500
74000
74500
75000
75500
76000
76500
77000
77500
78000
78500
79000
79500
80000
80500
81000
81500
82000
82500
83000
83500
84000
84500
8500

In [35]:
title_body_only = pd.DataFrame(normal_body)
title_body_only.shape

(182792, 1)

In [36]:
final_title_body = pd.DataFrame()
final_title_body = pd.concat([final_title_body, pd.DataFrame(codes_data['Title']).reset_index(drop=True), title_body_only], axis=1, ignore_index=True).reset_index(drop=True)

In [37]:
code_only_df = pd.DataFrame(code_body)
print(code_only_df.shape)
labels = code_d[:, 7]
final_code = pd.DataFrame()
final_code = pd.concat([code_only_df, final_title_body, pd.DataFrame(labels)], axis=1, ignore_index=True).reset_index(drop=True)

(182792, 1)


In [38]:
final_code_nonnull = final_code[final_code[0]!=''].reset_index(drop=True)

In [ ]:
final_code_nonnull

In [39]:
label_y = []
lang = ["java", "javascript", "c#"]
for i in range(final_code_nonnull.shape[0]):
    
    ta = final_code_nonnull[3][i].split(",")
    l = [x for x in ta if x in lang]
    label_y.append(l[0])
#     final_code_nonnull.at[i, 3] = l[0]

In [40]:
final_df = pd.DataFrame()
final_df = pd.concat([final_df, final_code_nonnull, pd.DataFrame(label_y)], axis=1, ignore_index=True).reset_index(drop=True)

In [41]:
final_df.shape

(156420, 5)

In [ ]:
final_code_nonnull.to_csv("Final_Code_Body_All.csv", index=False)

In [42]:
final_df_list = final_df.copy()

for i in range(final_df_list.shape[0]):
    
    if i%500==0:
        print(i)
    q1 = final_df_list[3][i]
    q2 = final_df_list[4][i]
    q1 = q1.split(",")
    q2 = q2.split(",")
    final_df_list.at[i,3] = q1
    final_df_list.at[i,4] = q2


0
500
1000
1500
2000
2500
3000
3500
4000
4500
5000
5500
6000
6500
7000
7500
8000
8500
9000
9500
10000
10500
11000
11500
12000
12500
13000
13500
14000
14500
15000
15500
16000
16500
17000
17500
18000
18500
19000
19500
20000
20500
21000
21500
22000
22500
23000
23500
24000
24500
25000
25500
26000
26500
27000
27500
28000
28500
29000
29500
30000
30500
31000
31500
32000
32500
33000
33500
34000
34500
35000
35500
36000
36500
37000
37500
38000
38500
39000
39500
40000
40500
41000
41500
42000
42500
43000
43500
44000
44500
45000
45500
46000
46500
47000
47500
48000
48500
49000
49500
50000
50500
51000
51500
52000
52500
53000
53500
54000
54500
55000
55500
56000
56500
57000
57500
58000
58500
59000
59500
60000
60500
61000
61500
62000
62500
63000
63500
64000
64500
65000
65500
66000
66500
67000
67500
68000
68500
69000
69500
70000
70500
71000
71500
72000
72500
73000
73500
74000
74500
75000
75500
76000
76500
77000
77500
78000
78500
79000
79500
80000
80500
81000
81500
82000
82500
83000
83500
84000
84500
8500

In [322]:
final_df_list

0  \
0       public partial class Answer\n{\n    public int...   
1               File file = new File(fullPath, "uoc" +...   
2       $scope.properties = [{\n    title: "Tai's Bull...   
3       var geolocationProvider = new Microsoft.Maps\n...   
4       // compose a message function\n$('#send_messag...   
5       http://local/Home/CallGrid?_search=true&nd=138...   
6       import java.net.*;\nimport java.util.*;\nimpor...   
7       GridLayout.spec() GridLayout.LayoutParms param...   
8       mobireportsrestapp <web-app \nxmlns:xsi="http:...   
9                                             closePath()   
10       14's sum=0 with wastage:0   And combination:0...   
11      ArrayList<String> for(PeopleDetails person : p...   
12      <form action="#" method="POST" name="logon" id...   
13                                    .exe .exe .exe .apk   
14                                         User User User   
15      $("<h2/>")\n.html("oSingle.hooks.m4a")\n.appen...   
16      var trackUrl = 'THE_URL';\nvar Client_ID = 'CL...   
17      JList Messageboard JList JPanels JScrollPane p...   
18      {\n  "manifest_version": 2,\n  "name": "1tst",...   
19      XMLHttpRequest undefined "" function insertMes...   
20      Class A { \n    public static int A = 1;\n    ...   
21      using System;\nusing System.Collections.Generi...   
22      DbxEntry.File uploadedFile = client.uploadFile...   
23          private void button3_Click_1(object sender...   
24      app.js var express = require('express');\nvar ...   
25      PictureBox[] pics = {picBackGround, picBackGro...   
26        <span ng-show="{{ save_state == 'saved' }}">...   
27        for (var i = 0; i < menuitems.length; i++){ ...   
28      public ArrayList<Log> selectAllLogs(){\n    if...   
29      public class SomeGuiClass{\n    private static...   
...                                                   ...   
156390  define(\n    [\n        'Extension_Name/js/vie...   
156391  angular.module('app').controller('demo', demo)...   
156392  forms-elements.js:87 \nUncaught ReferenceError...   
156393  @RequestMapping(method = RequestMethod.POST,\n...   
156394  <tr>\n    <th>Year</th>\n    <td><input type="...   
156395  private void PlayerClockInPanelControl_Load(ob...   
156396  public List<EcoConfigPrioridadLead> getAllPrio...   
156397  // Keep showing "Exception thrown" message.\ns...   
156398  <div id="printableArea">\n<div align="center">...   
156399  debounce setTimeout setInterval(function() {\n...   
156400  public class Application extends Controller {\...   
156401  Application.StartupPath MainFolder\n  - Crysta...   
156402  GetObjectRequest request = new GetObjectReques...   
156403  <div>\n      <textarea id="ta" onpaste="functi...   
156404  DeviceInformationCollection    private async v...   
156405  func getCredential() -> String {\n\n    let se...   
156406  {"page":"www.abc.com","impressions":1,"positio...   
156407  var uri = 'sharepointmodel.json';\nvar uri2 = ...   
156408  <!DOCTYPE html>\r\n<html>\r\n<body>\r\n\r\nRad...   
156409  <table md-table flex-order-gt-sm >\n  <thead m...   
156410           var file = new FileInfo(doc.FullName);\n   
156411      AWSCredentials credentails = new BasicAWSC...   
156412  @[a-zA-Z0-9_-]* (?<=^|(?<=[^a-zA-Z0-9-_\\.]))@...   
156413  /**\r\n  * Helper function for returning a gri...   
156414  var privateKey = fs.readFileSync( 'key.pem' );...   
156415  The system requirement are not meet. Your Java...   
156416  package test;\n\nimport java.net.URL;\nimport ...   
156417  Click HERE     <div style="cursor: pointer;" i...   
156418  sql = "SELECT (SELECT * FROM Data WHERE Produc...   
156419  import { NgModule }      from '@angular/core';...   

                                                        1  \
0            DB ViewModel Data not Displaying in MVC View   
1                                Decrypt pixels of bitmap   
2       Using $http to load Angular JS json file not w...   
3       Why is the location p

In [323]:
final_df_list.to_csv("Final_wo_preprocessing_JAVA_C#_JAVASCRIPT.csv", index=False)

In [388]:
final_df_list

0  \
0       public partial class Answer\n{\n    public int...   
1               File file = new File(fullPath, "uoc" +...   
2       $scope.properties = [{\n    title: "Tai's Bull...   
3       var geolocationProvider = new Microsoft.Maps\n...   
4       // compose a message function\n$('#send_messag...   
5       http://local/Home/CallGrid?_search=true&nd=138...   
6       import java.net.*;\nimport java.util.*;\nimpor...   
7       GridLayout.spec() GridLayout.LayoutParms param...   
8       mobireportsrestapp <web-app \nxmlns:xsi="http:...   
9                                             closePath()   
10       14's sum=0 with wastage:0   And combination:0...   
11      ArrayList<String> for(PeopleDetails person : p...   
12      <form action="#" method="POST" name="logon" id...   
13                                    .exe .exe .exe .apk   
14                                         User User User   
15      $("<h2/>")\n.html("oSingle.hooks.m4a")\n.appen...   
16      var trackUrl = 'THE_URL';\nvar Client_ID = 'CL...   
17      JList Messageboard JList JPanels JScrollPane p...   
18      {\n  "manifest_version": 2,\n  "name": "1tst",...   
19      XMLHttpRequest undefined "" function insertMes...   
20      Class A { \n    public static int A = 1;\n    ...   
21      using System;\nusing System.Collections.Generi...   
22      DbxEntry.File uploadedFile = client.uploadFile...   
23          private void button3_Click_1(object sender...   
24      app.js var express = require('express');\nvar ...   
25      PictureBox[] pics = {picBackGround, picBackGro...   
26        <span ng-show="{{ save_state == 'saved' }}">...   
27        for (var i = 0; i < menuitems.length; i++){ ...   
28      public ArrayList<Log> selectAllLogs(){\n    if...   
29      public class SomeGuiClass{\n    private static...   
...                                                   ...   
156390  define(\n    [\n        'Extension_Name/js/vie...   
156391  angular.module('app').controller('demo', demo)...   
156392  forms-elements.js:87 \nUncaught ReferenceError...   
156393  @RequestMapping(method = RequestMethod.POST,\n...   
156394  <tr>\n    <th>Year</th>\n    <td><input type="...   
156395  private void PlayerClockInPanelControl_Load(ob...   
156396  public List<EcoConfigPrioridadLead> getAllPrio...   
156397  // Keep showing "Exception thrown" message.\ns...   
156398  <div id="printableArea">\n<div align="center">...   
156399  debounce setTimeout setInterval(function() {\n...   
156400  public class Application extends Controller {\...   
156401  Application.StartupPath MainFolder\n  - Crysta...   
156402  GetObjectRequest request = new GetObjectReques...   
156403  <div>\n      <textarea id="ta" onpaste="functi...   
156404  DeviceInformationCollection    private async v...   
156405  func getCredential() -> String {\n\n    let se...   
156406  {"page":"www.abc.com","impressions":1,"positio...   
156407  var uri = 'sharepointmodel.json';\nvar uri2 = ...   
156408  <!DOCTYPE html>\r\n<html>\r\n<body>\r\n\r\nRad...   
156409  <table md-table flex-order-gt-sm >\n  <thead m...   
156410           var file = new FileInfo(doc.FullName);\n   
156411      AWSCredentials credentails = new BasicAWSC...   
156412  @[a-zA-Z0-9_-]* (?<=^|(?<=[^a-zA-Z0-9-_\\.]))@...   
156413  /**\r\n  * Helper function for returning a gri...   
156414  var privateKey = fs.readFileSync( 'key.pem' );...   
156415  The system requirement are not meet. Your Java...   
156416  package test;\n\nimport java.net.URL;\nimport ...   
156417  Click HERE     <div style="cursor: pointer;" i...   
156418  sql = "SELECT (SELECT * FROM Data WHERE Produc...   
156419  import { NgModule }      from '@angular/core';...   

                                                        1  \
0            DB ViewModel Data not Displaying in MVC View   
1                                Decrypt pixels of bitmap   
2       Using $http to load Angular JS json file not w...   
3       Why is the location p

In [43]:
X_code = pd.DataFrame(final_df[0])
y_code = pd.DataFrame(final_df_list[4])

In [44]:
for i in range(X_code.shape[0]):
    numbers = remove_numbers(X_code.iloc[i][0])
    lowers = lowercase(numbers)
    tokenized = remove_punctuation(lowers)
    tokenized = tokenization(tokenized)
    tokenized = remove_numbers_from_list(tokenized)
    tokenized = ' '.join(tokenized)
    X_code.at[i,0] = tokenized

In [45]:
U_code = pd.DataFrame()
U_code = pd.concat([U_code,X_code,y_code], axis=1, ignore_index=True).reset_index(drop=True)

In [46]:
# tempX = pd.DataFrame(U[0])
# tempY = pd.DataFrame(U[1])

In [47]:
# Importing sklearn required libraries
from sklearn.preprocessing import MultiLabelBinarizer
from sklearn.feature_extraction.text import TfidfVectorizer
from scipy.sparse import coo_matrix, hstack
from sklearn.svm import LinearSVC

In [48]:
multilabel_binarizer = MultiLabelBinarizer()
y_bin = multilabel_binarizer.fit_transform(U_code[1].values)

In [49]:
def evaluation_metrics(y_actual, y_predicted):
    
    accuracy = accuracy_score(y_actual, y_predicted)
    print("Accuracy:", accuracy)
    recall = recall_score(y_actual, y_predicted, average='micro')
    print("Recall:", recall)
    precision = precision_score(y_actual, y_predicted, average='micro')
    print("Precision:", precision)
    f1 = f1_score(y_actual, y_predicted, average='micro')
    print("F1-Score:", f1)
    hamming = hamming_loss(y_actual, y_predicted)
    print("Hamming Loss:", hamming)
    jaccard = jaccard_similarity_score(y_actual, y_predicted)
    print("Jaccard Similarity Score:", jaccard)
    return accuracy, recall, precision, f1, hamming, jaccard

# ONLY CODE PART

In [50]:
from sklearn.model_selection import train_test_split
X_train, X_test, y_train, y_test = train_test_split(U_code[0].values, y_bin, test_size = 0.3, random_state = 0)

In [51]:
X_train_tfidf, tfidf = calculate_tfidf_vector(X_train.ravel())
X_test_tfidf = tfidf.transform(X_test.ravel())

In [52]:
def apply_model(classifier, X_Train, y_Train, X_Test, y_Test):
    
    clf = OneVsRestClassifier(classifier)
    clf.fit(X_Train, y_Train)
    y_Pred = clf.predict(X_Test)
    
    accuracy = clf.score(X_Test, y_Test)
    
    return accuracy, y_Pred, clf

In [53]:
from sklearn.multiclass import OneVsRestClassifier
from sklearn.metrics import classification_report

In [54]:
from sklearn.naive_bayes import MultinomialNB
mn = MultinomialNB()
mn_accuracy, mn_y_pred, mn_code = apply_model(mn, X_train_tfidf, y_train, X_test_tfidf, y_test)

In [55]:
print(mn_accuracy)
print(classification_report(y_test, mn_y_pred))


0.8016664535651877
              precision    recall  f1-score   support

           0       0.94      0.68      0.79     11468
           1       0.91      0.81      0.86     15635
           2       0.92      0.88      0.90     19823

   micro avg       0.92      0.81      0.86     46926
   macro avg       0.93      0.79      0.85     46926
weighted avg       0.92      0.81      0.86     46926
 samples avg       0.81      0.81      0.81     46926



c:\python\lib\site-packages\sklearn\metrics\classification.py:1143: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 in samples with no predicted labels.
  'precision', 'predicted', average, warn_for)


In [57]:
from sklearn.metrics import accuracy_score
mn_code_accuracy, mn_code_recall, mn_code_precision, mn_code_f1, mn_code_hamming, mn_code_jaccard = evaluation_metrics(y_test, mn_y_pred)

Accuracy: 0.8016664535651877
Recall: 0.8085709414823339
Precision: 0.9237717290743536
F1-Score: 0.862340909090909
Hamming Loss: 0.0860503771896177
Jaccard Similarity Score: 0.8051186975237609


In [58]:
svc = LinearSVC()
svc_accuracy, svc_y_pred_code, clf_svc_code = apply_model(svc, X_train_tfidf, y_train, X_test_tfidf, y_test)

In [59]:
print(svc_accuracy)
print(classification_report(y_test, svc_y_pred_code))

0.8258534714230916
              precision    recall  f1-score   support

           0       0.90      0.75      0.82     11468
           1       0.91      0.84      0.87     15635
           2       0.92      0.89      0.91     19823

   micro avg       0.91      0.84      0.87     46926
   macro avg       0.91      0.83      0.87     46926
weighted avg       0.91      0.84      0.87     46926
 samples avg       0.83      0.84      0.84     46926



c:\python\lib\site-packages\sklearn\metrics\classification.py:1143: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 in samples with no predicted labels.
  'precision', 'predicted', average, warn_for)


In [60]:
svc_code_accuracy, svc_code_recall, svc_code_precision, svc_code_f1, svc_code_hamming, svc_code_jaccard = evaluation_metrics(y_test, svc_y_pred_code)

Accuracy: 0.8258534714230916
Recall: 0.8396624472573839
Precision: 0.9127383075818295
F1-Score: 0.8746767301182085
Hamming Loss: 0.08020429328446206
Jaccard Similarity Score: 0.8327579593402378


In [61]:
final_df_list

0  \
0       public partial class Answer\n{\n    public int...   
1               File file = new File(fullPath, "uoc" +...   
2       $scope.properties = [{\n    title: "Tai's Bull...   
3       var geolocationProvider = new Microsoft.Maps\n...   
4       // compose a message function\n$('#send_messag...   
5       http://local/Home/CallGrid?_search=true&nd=138...   
6       import java.net.*;\nimport java.util.*;\nimpor...   
7       GridLayout.spec() GridLayout.LayoutParms param...   
8       mobireportsrestapp <web-app \nxmlns:xsi="http:...   
9                                             closePath()   
10       14's sum=0 with wastage:0   And combination:0...   
11      ArrayList<String> for(PeopleDetails person : p...   
12      <form action="#" method="POST" name="logon" id...   
13                                    .exe .exe .exe .apk   
14                                         User User User   
15      $("<h2/>")\n.html("oSingle.hooks.m4a")\n.appen...   
16      var trackUrl = 'THE_URL';\nvar Client_ID = 'CL...   
17      JList Messageboard JList JPanels JScrollPane p...   
18      {\n  "manifest_version": 2,\n  "name": "1tst",...   
19      XMLHttpRequest undefined "" function insertMes...   
20      Class A { \n    public static int A = 1;\n    ...   
21      using System;\nusing System.Collections.Generi...   
22      DbxEntry.File uploadedFile = client.uploadFile...   
23          private void button3_Click_1(object sender...   
24      app.js var express = require('express');\nvar ...   
25      PictureBox[] pics = {picBackGround, picBackGro...   
26        <span ng-show="{{ save_state == 'saved' }}">...   
27        for (var i = 0; i < menuitems.length; i++){ ...   
28      public ArrayList<Log> selectAllLogs(){\n    if...   
29      public class SomeGuiClass{\n    private static...   
...                                                   ...   
156390  define(\n    [\n        'Extension_Name/js/vie...   
156391  angular.module('app').controller('demo', demo)...   
156392  forms-elements.js:87 \nUncaught ReferenceError...   
156393  @RequestMapping(method = RequestMethod.POST,\n...   
156394  <tr>\n    <th>Year</th>\n    <td><input type="...   
156395  private void PlayerClockInPanelControl_Load(ob...   
156396  public List<EcoConfigPrioridadLead> getAllPrio...   
156397  // Keep showing "Exception thrown" message.\ns...   
156398  <div id="printableArea">\n<div align="center">...   
156399  debounce setTimeout setInterval(function() {\n...   
156400  public class Application extends Controller {\...   
156401  Application.StartupPath MainFolder\n  - Crysta...   
156402  GetObjectRequest request = new GetObjectReques...   
156403  <div>\n      <textarea id="ta" onpaste="functi...   
156404  DeviceInformationCollection    private async v...   
156405  func getCredential() -> String {\n\n    let se...   
156406  {"page":"www.abc.com","impressions":1,"positio...   
156407  var uri = 'sharepointmodel.json';\nvar uri2 = ...   
156408  <!DOCTYPE html>\r\n<html>\r\n<body>\r\n\r\nRad...   
156409  <table md-table flex-order-gt-sm >\n  <thead m...   
156410           var file = new FileInfo(doc.FullName);\n   
156411      AWSCredentials credentails = new BasicAWSC...   
156412  @[a-zA-Z0-9_-]* (?<=^|(?<=[^a-zA-Z0-9-_\\.]))@...   
156413  /**\r\n  * Helper function for returning a gri...   
156414  var privateKey = fs.readFileSync( 'key.pem' );...   
156415  The system requirement are not meet. Your Java...   
156416  package test;\n\nimport java.net.URL;\nimport ...   
156417  Click HERE     <div style="cursor: pointer;" i...   
156418  sql = "SELECT (SELECT * FROM Data WHERE Produc...   
156419  import { NgModule }      from '@angular/core';...   

                                                        1  \
0            DB ViewModel Data not Displaying in MVC View   
1                                Decrypt pixels of bitmap   
2       Using $http to load Angular JS json file not w...   
3       Why is the location p

In [62]:
final_df_title_body = final_df_list[[1,2,3]]
final_df_title_body = final_df_title_body.rename(columns={1: 'Title', 2: 'Body', 3:'Tag'})


In [63]:
full = preprocessing(final_df_title_body)

In [89]:
full

Title  \
0                   db viewmodel data displaying mvc view   
1                                    decrypt pixel bitmap   
2       using http load angular j json file working fi...   
3       location provided redundantly two different pl...   
4                using ajaxform plugin view ajax response   
5          add column search filter jqgrid severside code   
6                serversocket communication client socket   
7                           understand use gridlayoutspec   
8               unknown error rest application deployment   
9       change color next line drawing without closing...   
10      need best combination array element specific s...   
11                           iterate item arraylist index   
12                            casperjs submit form action   
13                new java understanding java compilation   
14      create single entity existing entity using que...   
15                             loop jquery appending html   
16            get soundcloud embed code soundcloudcom url   
17               correctly update jlist modifying content   
18                      chrome extension sendmessages one   
19                         ajax post returning null value   
20                     use enums java different datatypes   
21                      c# processmemoryreaderlib working   
22                      check dropbox progress large file   
23      webclient stripping newlines file using downlo...   
24       expensive require something within expressjs app   
25                        array variable used like method   
26             directive responding change scope variable   
27                      repeating loop resetting variable   
28       ca fine error operation allowed resultset closed   
29                          shared memory thread updating   
...                                                   ...   
156390           requirejs dependency loading firefox esr   
156391  angulargrid library produce empty space specia...   
156392  script loading browser error uncaught referenc...   
156393                            bad request spring rest   
156394  number text input along image file angularjs h...   
156395                            timerstart unexpectedly   
156396             hibernate manytomany relationship work   
156397  visual studio suppress certain exception throw...   
156398            fill input field json data sent printer   
156399                            use debounce settimeout   
156400                   set action aws java sdk iot rule   
156401  find report file outside applicationstartuppat...   
156402  s3 clientgetobject behaviour read beyond filesize   
156403                             highlight text textbox   
156404     cannot use deviceinformationcollection library   
156405             aes encryption swift cannot decrypt c#   
156406      filter data without repeat value mongodb java   
156407               retrieving multiple json file jquery   
156408                  problem focus input radio firefox   
156409                         nested ngrepeat one depend   
156410              file path working one drive buisiness   
156411  downloading s3 file give date parsing error pa...   
156412        find twitter mention using regex java twist   
156413                     protractor e2e testing ui grid   
156414  setup node http server using ssl certificate g...   
156415              javafx error accessing sap gui centos   
156416                xsd element name resolved unit test   
156417                     alert last cat show full image   
156418  error written subquery return one field withou...   
156419   ca bind control since known property mycomponent   

                                                     Body  \
0       new c# mvc probably obvious error controller l...   
1       app encrypts pixel image decrypts encryption c...   
2       present load bunch json using following try wo...   
3       playing around bi

In [90]:
X_title = pd.DataFrame(full['Title'])
X_body = pd.DataFrame(full['Body'])
y_body = pd.DataFrame(full['Tag'])

In [91]:
final_df_title_body

Title  \
0            DB ViewModel Data not Displaying in MVC View   
1                                Decrypt pixels of bitmap   
2       Using $http to load Angular JS json file not w...   
3       Why is the location provided redundantly at tw...   
4       Using ajaxForm plugin on view that is itself a...   
5       How do you add column search filter on JqGrid ...   
6             ServerSocket communication to client Socket   
7           Don't understand how to use GridLayout.spec()   
8        Unknown Error For my Rest Application Deployment   
9       Change color for the next line I'm drawing, wi...   
10      Need best combination of array elements for sp...   
11      Iterate through items in arraylist, with an index   
12      Casperjs: how can I submit a form that has act...   
13           new to java - understanding java compilation   
14      Create a single entity for each of existing en...   
15                 If loop in jquery while appending html   
16      How to get Soundcloud embed code by soundcloud...   
17      Correctly update JList after modifying its con...   
18            chrome extension sendMessages more than one   
19                        AJAX POST returning null values   
20          use of Enums in java with different datatypes   
21                  c# ProcessMemoryReaderLib not working   
22                  Check dropbox progress on large files   
23      WebClient is stripping newlines from files whe...   
24      How expensive is it to require() something wit...   
25      "array of x is a 'variable' but is used like a...   
26      Directive not responding to changes in scope v...   
27       Repeating a for loop by re-setting variable to 0   
28      Can't fine the error with Operation not allowe...   
29             Shared memory between threads not updating   
...                                                   ...   
156390  require.js dependency loading in Firefox ESR 4...   
156391  AngularGrid library produces empty space in so...   
156392  Scripts not loading in browser with error Unca...   
156393                   400 Bad Request with spring REST   
156394  Number of text input along with image file fro...   
156395                        Timer.start() unexpectedly?   
156396      Hibernate @ManyToMany relationship don't work   
156397  Visual Studio - suppress certain "Exception th...   
156398  fill input fields with json data then sent to ...   
156399                         Use debounce in setTimeout   
156400   How to set Actions in aws java sdk for iot rule?   
156401  Find report file outside of Application.Startu...   
156402  S3 client.GetObject behaviour if read beyond f...   
156403       How can I highlight the text In the textbox?   
156404     Cannot use DeviceInformationCollection library   
156405       AES Encryption in Swift cannot decrypt in C#   
156406  How to filter data without repeat values in mo...   
156407         retrieving multiple JSON files with jquery   
156408  Problems with focus() in an input radio in Fir...   
156409      nested ng-repeat that one depend on the other   
156410  File path when working with One Drive for Buis...   
156411  Downloading S3 file gives date parsing error f...   
156412  Find a Twitter mention using Regex in Java (wi...   
156413                     Protractor e2e Testing ui grid   
156414  Setup node https server using SSL certificate ...   
156415     JavaFX error while accessing SAP GUI on centOS   
156416         xsd element name not resolved in unit test   
156417        How to alert when last cat show full image?   
156418  Error: You have written a subquery that can re...   
156419  Can't bind to 'control' since it isn't a known...   

                                                     Body  \
0       New to C# and MVC, so probably an obvious erro...   
1       I have an app that encrypts the pixels of an i...   
2       At present I can load a bunch of JSON using th...   
3       I'm playing aroun

In [92]:
y_body = pd.DataFrame(final_df_title_body['Tag'])

In [93]:
U_title = pd.DataFrame()
U_title = pd.concat([U_title,X_title,y_body], axis=1, ignore_index=True).reset_index(drop=True)

U_body = pd.DataFrame()
U_body = pd.concat([U_body, X_body, y_body], axis=1, ignore_index=True).reset_index(drop=True)

# TITLE PART ONLY

In [149]:
multilabel_binarizer_title = MultiLabelBinarizer()
y_bin_title = multilabel_binarizer_title.fit_transform(U_title[1].values)

In [153]:
y_bin_title.shape

(156420, 14523)

In [150]:
X_train_title, X_test_title, y_train_title, y_test_title = train_test_split(U_title[0].values, y_bin_title, test_size = 0.3, random_state = 0)

In [151]:
X_train_title_tfidf, tfidf_title = calculate_tfidf_vector(X_train_title.ravel())
X_test_title_tfidf = tfidf_title.transform(X_test_title.ravel())

In [152]:
mn_accuracy, mn_y_pred = apply_model(mn, X_train_title_tfidf, y_train_title, X_test_title_tfidf, y_test_title)
print(mn_accuracy)
# print(classification_report(y_test, mn_y_pred))

MemoryError: 

In [88]:
svc = LinearSVC()
svc_accuracy, svc_y_pred = apply_model(svc, X_train_title_tfidf, y_train_title, X_test_title_tfidf, y_test_title)
print(svc_accuracy)
# print(classification_report(y_test, svc_y_pred))

NameError: name 'X_train_title_tfidf' is not defined

# BODY PART ONLY

In [63]:
multilabel_binarizer_body = MultiLabelBinarizer()
y_bin_body = multilabel_binarizer_body.fit_transform(U_body[1].values)

(156420, 42)

In [64]:
X_train_body, X_test_body, y_train_body, y_test_body = train_test_split(U_body[0].values, y_bin_body, test_size = 0.3, random_state = 0)

In [65]:
X_train_body_tfidf, tfidf_body = calculate_tfidf_vector(X_train_body.ravel())
X_test_body_tfidf = tfidf_body.transform(X_test_body.ravel())

In [66]:
mn_accuracy, mn_y_pred = apply_model(mn, X_train_body_tfidf, y_train_body, X_test_body_tfidf, y_test_body)
print(mn_accuracy)
# print(classification_report(y_test, mn_y_pred))

0.013148361249627073


In [67]:
svc = LinearSVC()
svc_accuracy, svc_y_pred = apply_model(svc, X_train_body_tfidf, y_train_body, X_test_body_tfidf, y_test_body)
print(svc_accuracy)
# print(classification_report(y_test, svc_y_pred))

0.03803861398798108


# BODY & TITLE PART 

In [68]:
U_title_body = pd.DataFrame()
U_title_body = pd.concat([U_title_body,X_title,X_body,y_body], axis=1, ignore_index=True).reset_index(drop=True)

In [70]:
X_train_title_body, X_test_title_body, y_train_title_body, y_test_title_body = train_test_split(U_title_body[0].values, y_bin_body, test_size = 0.3, random_state = 0)

In [75]:
X_train_title_body_tfidf, tfidf_title_body = calculate_tfidf_vector(X_train_title_body.ravel())
X_test_title_body_tfidf = tfidf_title_body.transform(X_test_title_body.ravel())

In [76]:
mn_accuracy, mn_y_pred = apply_model(mn, X_train_title_body_tfidf, y_train_title_body, X_test_title_body_tfidf, y_test_title_body)
print(mn_accuracy)
# print(classification_report(y_test, mn_y_pred))

0.025295145548310104


In [77]:
svc = LinearSVC()
svc_accuracy, svc_y_pred = apply_model(svc, X_train_title_body_tfidf, y_train_title_body, X_test_title_body_tfidf, y_test_title_body)
print(svc_accuracy)
# print(classification_report(y_test, svc_y_pred))

0.06243873332480927


In [93]:
print(svc_y_pred)
print(y_test_title_body)


[[1 0 0 ... 0 0 0]
 [1 0 0 ... 0 0 0]
 [1 1 0 ... 0 0 0]
 ...
 [1 0 0 ... 0 0 0]
 [1 0 0 ... 0 0 0]
 [1 1 0 ... 0 1 0]]
[[1 1 1 ... 0 0 0]
 [1 0 0 ... 0 0 0]
 [1 1 0 ... 0 1 0]
 ...
 [1 0 0 ... 0 0 0]
 [1 0 0 ... 0 0 0]
 [1 1 0 ... 0 1 0]]


In [80]:
from sklearn.metrics import jaccard_similarity_score
jaccard_similarity_score(y_test_title_body, svc_y_pred)

0.7143062614736972

In [104]:
c=0
for j in range (len(y_test_title_body)):
    count=0
    for k in range (len(y_test_title_body[j])):
        if(svc_y_pred[j][k]==y_test_title_body[j][k]==1):
            count=count+1
    if(count>=11):
        c=c+1
print(c)
print(c/len(svc_y_pred))

31660
0.674679282274219


In [105]:
for i in range(y_test_title_body.shape[0]):
    print(y_test_title_body[i])

[1 1 1 1 1 0 0 0 0 0 0 0 0 0 0 0 1 1 1 0 1 0 1 1 1 0 0 0 0 1 1 0 0 1 1 1 0
 0 0 0 0 0]
[1 0 0 1 0 0 0 0 0 0 0 0 0 0 0 0 1 1 1 0 1 0 0 0 1 1 0 1 0 1 1 0 0 1 1 1 0
 1 0 0 0 0]
[1 1 0 1 1 0 0 0 0 0 0 0 0 0 0 0 0 1 1 1 1 0 0 0 1 0 0 1 0 0 0 0 1 1 0 0 1
 0 0 0 1 0]
[1 0 0 1 1 0 0 0 0 0 0 0 0 0 0 0 1 0 0 1 1 0 1 0 1 1 0 0 0 1 0 0 0 0 1 1 1
 1 0 0 0 0]
[1 0 0 1 1 0 0 0 0 0 0 0 0 0 0 0 1 1 1 1 0 0 0 0 1 1 0 0 0 0 1 1 0 1 1 1 0
 1 0 1 0 0]
[1 0 0 1 0 0 0 0 0 0 0 0 0 0 0 0 1 0 1 0 1 0 0 1 1 1 0 0 0 1 1 1 1 1 1 1 1
 1 0 1 1 0]
[1 0 0 1 1 0 0 0 0 0 0 0 0 0 0 0 1 0 1 1 1 1 1 1 1 1 0 1 1 1 1 1 0 1 1 1 1
 1 0 0 0 0]
[1 0 0 1 1 0 0 0 0 1 0 0 0 0 0 0 1 1 1 0 1 0 0 0 1 1 0 0 0 0 1 1 1 1 1 1 1
 1 1 0 1 0]
[1 0 0 1 0 0 0 0 0 0 0 0 0 0 0 0 1 0 0 1 1 0 0 0 1 1 0 0 1 1 1 0 0 1 0 0 0
 1 0 0 0 0]
[1 1 0 1 1 1 0 0 0 0 0 0 0 0 0 0 0 0 1 0 1 1 0 0 0 0 0 0 0 1 0 0 0 1 1 1 0
 0 1 0 0 0]
[1 1 0 1 1 1 0 0 0 0 1 0 0 0 0 0 1 1 1 0 1 0 0 0 1 0 0 1 1 1 0 1 0 0 1 1 0
 1 1 0 0 0]
[1 0 0 1 0 0 0 0 0 0 0 0 0 0 0 0 1 0 1 0 1 

 1 0 0 0 0]
[1 1 0 1 0 1 0 0 0 0 0 0 0 0 0 0 1 0 1 1 1 1 0 0 1 0 0 0 1 1 1 1 0 0 1 1 0
 0 0 0 1 0]
[1 0 0 1 0 1 0 0 0 0 0 0 0 0 0 0 1 0 1 1 1 0 0 0 1 1 0 1 0 1 1 1 1 1 1 1 1
 1 0 0 0 1]
[1 1 0 1 0 0 0 0 0 0 0 0 0 0 0 0 1 0 1 0 1 0 0 0 1 1 0 1 0 1 1 0 0 1 1 1 0
 0 0 0 0 1]
[1 0 0 1 0 0 0 0 1 0 0 0 0 0 0 0 1 0 1 1 0 0 1 0 1 1 0 1 0 1 0 1 0 1 1 1 1
 1 0 0 0 0]
[1 1 0 1 1 0 0 0 0 0 0 0 0 0 0 0 1 0 1 0 1 0 0 0 0 0 0 0 0 1 1 1 0 1 0 1 0
 0 0 0 1 0]
[1 1 0 1 0 1 0 0 0 0 0 0 0 0 0 0 1 0 1 0 1 0 0 0 1 1 0 0 0 1 0 1 1 1 1 1 1
 1 0 1 1 0]
[1 0 0 1 1 0 0 0 0 0 0 0 0 0 0 0 1 1 1 1 1 0 1 1 1 1 0 1 0 1 1 1 0 1 1 1 1
 1 0 0 1 0]
[1 0 0 1 1 0 0 0 0 0 0 0 0 0 0 0 1 0 1 0 1 0 1 0 1 1 0 1 1 1 1 1 0 1 1 1 0
 1 0 1 0 0]
[1 0 0 1 1 1 1 1 0 0 0 0 0 0 0 0 1 0 1 0 1 0 0 0 1 1 0 1 1 1 1 1 0 1 1 1 0
 1 0 0 1 1]
[1 0 0 1 1 0 0 0 0 0 0 0 0 0 0 0 1 0 0 0 1 0 0 1 0 1 1 1 1 0 0 1 0 0 1 0 1
 1 0 0 1 0]
[1 1 0 1 0 1 0 0 0 0 0 0 0 0 0 0 1 0 1 1 1 0 1 0 1 0 0 0 0 1 0 1 0 1 1 1 0
 1 1 0 0 0]
[1 0 0 1 0 0 0 0 0 0 0 0 0 0 0 

 1 0 0 0 0]
[1 0 0 1 1 0 0 0 0 0 0 0 0 0 0 0 1 0 1 1 1 0 1 1 1 1 0 1 0 1 1 1 0 0 0 1 0
 1 0 1 0 0]
[1 0 0 1 0 0 0 0 0 0 0 0 0 0 0 0 1 0 1 0 1 0 0 0 1 1 0 0 0 0 0 1 1 1 1 1 1
 1 0 0 1 0]
[1 0 0 1 1 0 0 0 0 0 0 0 0 0 0 0 1 1 1 0 1 1 1 0 1 1 0 1 1 1 1 0 0 0 1 1 0
 1 0 0 0 0]
[1 0 0 1 1 0 0 0 0 1 0 0 0 0 0 0 1 0 1 0 1 0 1 0 1 1 0 1 1 0 1 1 1 1 1 1 1
 1 0 0 1 0]
[1 1 0 1 0 0 0 0 0 0 0 0 0 0 0 0 0 0 1 0 1 0 0 0 0 0 0 0 0 0 0 0 0 0 1 0 0
 0 1 0 0 0]
[1 1 0 1 1 0 1 1 1 0 0 0 0 0 0 0 1 0 1 1 1 1 1 0 1 0 0 1 1 1 1 0 0 1 1 1 1
 1 1 0 0 0]
[1 0 0 1 1 1 0 0 0 0 0 0 0 0 0 0 1 0 1 1 1 0 0 1 1 1 0 1 0 1 1 1 0 1 1 1 1
 1 0 0 0 0]
[1 0 0 1 0 1 0 0 0 0 0 0 0 0 0 0 1 1 1 0 1 0 0 0 1 1 1 0 0 1 1 1 1 1 1 1 1
 1 1 0 0 0]
[1 0 0 1 0 0 0 0 0 0 0 0 0 0 0 0 1 1 1 0 1 0 0 1 1 1 0 0 0 1 0 0 0 1 0 1 0
 1 0 0 0 0]
[0 1 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 1 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0
 0 0 0 0 0]
[1 0 0 1 1 0 0 0 0 0 0 0 0 0 0 0 1 0 1 1 1 1 1 0 1 1 0 1 1 1 1 0 0 1 1 1 0
 1 1 1 0 0]
[1 0 0 1 0 0 0 0 0 0 0 0 0 0 0 

[1 0 0 1 0 0 0 0 0 0 0 0 0 0 0 0 1 0 0 1 0 0 0 0 1 1 0 0 0 1 1 0 0 1 1 0 0
 1 0 0 0 0]
[1 0 0 1 0 0 0 0 0 0 0 0 0 0 0 0 1 0 0 1 0 0 0 0 1 1 0 0 0 1 1 0 0 1 0 0 0
 1 0 0 0 0]
[1 0 0 1 0 0 0 0 0 0 1 0 0 0 0 0 1 1 1 0 0 1 1 0 1 1 1 1 0 1 1 0 0 0 1 0 0
 1 0 0 0 0]
[1 0 0 1 0 0 0 0 0 0 0 0 0 0 0 0 1 0 0 1 1 0 1 1 1 1 0 1 1 1 0 1 0 1 1 1 1
 1 0 0 0 0]
[1 0 0 1 0 0 0 0 0 0 0 0 0 0 0 0 1 0 0 0 1 0 0 0 0 1 0 0 0 0 1 1 0 1 1 1 0
 1 0 0 0 0]
[1 0 0 1 0 0 0 0 0 0 0 0 0 0 0 0 1 0 0 0 0 0 0 0 0 1 0 1 0 0 0 1 0 0 1 1 0
 1 0 0 0 0]
[1 0 0 1 1 0 0 0 0 0 0 0 0 0 0 0 1 0 1 0 1 0 1 1 1 1 0 1 1 1 0 1 0 1 1 1 1
 1 0 0 0 0]
[1 0 0 1 0 0 0 0 0 0 0 0 0 0 0 0 1 0 1 1 1 1 0 1 1 1 0 1 1 1 1 0 0 1 1 1 0
 1 0 0 0 0]
[1 1 0 1 0 0 0 0 0 0 0 0 0 0 0 0 1 0 1 0 0 1 0 0 0 0 0 1 1 0 0 1 0 0 0 0 0
 0 1 1 0 0]
[1 0 0 1 0 0 0 0 0 0 0 0 0 0 0 0 1 0 1 0 1 0 0 0 1 1 0 1 0 0 0 1 0 0 1 0 0
 1 0 0 0 0]
[1 0 0 1 1 0 0 0 0 0 0 0 0 0 0 0 1 1 1 0 1 0 0 0 1 1 0 0 0 0 1 1 0 1 1 1 0
 1 0 0 1 0]
[1 0 0 1 0 0 0 0 0 0 0 0 0 0 0 0 1 0 1 0 0 

 1 0 0 1 0]
[1 0 0 1 0 0 0 0 0 0 0 0 0 0 0 0 1 0 1 0 1 0 0 1 1 1 0 1 1 0 0 1 1 1 1 1 1
 1 0 0 1 0]
[1 1 0 1 0 0 0 0 0 0 0 0 0 0 0 0 1 0 1 0 1 0 0 0 1 0 0 0 0 0 0 1 0 1 1 1 0
 0 0 0 0 0]
[1 1 0 1 1 1 0 0 0 0 0 0 0 0 0 0 1 0 1 1 1 0 0 1 1 0 0 1 1 1 1 1 0 0 1 1 0
 1 0 0 0 0]
[1 0 0 1 0 0 0 0 0 0 0 0 0 0 0 0 1 0 1 1 1 0 0 0 1 1 0 1 1 1 1 1 0 1 1 1 0
 1 0 0 0 0]
[0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 1 0 0 0 0 0 0 0 0 1 0 0 0 0 0 0 0 0 0 0 0
 1 0 0 0 0]
[1 0 0 1 0 0 0 0 0 0 0 0 0 0 0 0 1 0 1 0 1 0 0 0 1 1 0 1 0 0 1 1 1 1 1 1 1
 1 0 0 1 0]
[1 0 0 1 0 0 0 0 0 0 0 0 0 0 0 0 1 0 0 0 1 0 0 0 1 1 0 0 0 0 0 0 0 0 0 1 0
 1 0 1 0 0]
[1 0 0 1 0 0 0 0 0 0 0 0 0 0 0 0 1 0 1 0 1 0 0 0 1 1 0 1 0 0 0 1 0 0 1 0 0
 1 0 0 0 0]
[1 0 0 1 0 0 0 0 0 0 0 0 0 0 0 0 1 0 0 0 0 0 1 0 1 1 0 0 0 1 0 1 0 1 1 0 0
 1 0 0 0 0]
[1 1 0 1 0 1 0 0 0 0 0 0 0 0 0 0 1 0 1 0 1 0 0 0 0 1 0 0 0 1 1 0 0 1 1 1 0
 0 0 0 1 0]
[1 1 0 1 0 0 0 0 0 0 0 0 0 0 0 0 1 0 1 0 0 1 0 0 0 0 0 1 1 0 0 1 0 0 0 0 0
 0 1 1 0 0]
[1 0 0 1 0 1 0 0 0 0 0 0 0 0 0 

...

[1 0 0 1 0 0 0 0 0 0 0 0 0 0 0 0 1 0 0 0 0 0 1 0 1 1 0 0 0 1 1 1 0 1 1 0 0
 1 0 0 0 0]
[1 0 0 1 0 0 0 0 0 0 0 0 0 0 0 0 1 0 1 1 1 1 0 0 1 1 0 1 0 1 1 1 0 1 1 1 1
 1 0 1 0 0]
[1 0 0 1 0 0 0 0 0 0 0 0 0 0 0 0 1 0 1 0 1 0 0 1 1 1 0 1 1 0 0 1 1 1 1 1 1
 1 0 0 1 0]
[1 0 0 1 1 0 0 0 0 0 0 1 0 0 0 0 1 1 1 0 1 0 0 1 1 1 0 1 1 0 1 1 1 1 1 1 1
 1 1 0 1 0]
[1 0 0 1 1 0 0 0 0 0 0 0 1 0 0 0 1 0 1 0 1 0 0 0 1 1 0 0 1 0 1 1 0 1 1 1 0
 1 0 0 0 0]
[1 0 0 1 0 0 0 0 0 0 0 0 0 0 0 0 1 0 0 1 1 0 0 0 1 1 0 1 0 1 1 0 1 1 1 1 0
 1 0 0 0 0]
[1 0 0 1 0 0 0 0 0 0 0 0 0 0 0 0 1 1 0 1 1 1 1 1 1 1 0 1 0 1 0 0 0 1 1 1 1
 1 0 1 0 0]
[1 0 0 1 0 0 0 0 0 0 0 0 0 0 0 0 1 1 1 1 1 0 0 0 1 1 0 0 0 1 1 1 0 1 1 1 0
 1 1 0 0 0]
[1 1 0 1 0 1 0 0 0 0 0 0 0 0 0 0 1 0 1 0 1 0 1 0 1 1 0 0 0 1 1 1 0 1 1 1 0
 0 0 0 0 0]
[1 0 0 1 0 0 0 0 0 0 0 0 0 0 0 0 1 0 1 0 1 0 0 1 1 1 0 1 1 0 0 1 1 1 1 1 1
 1 0 0 1 0]
[1 1 0 1 1 1 0 0 0 0 0 0 0 0 0 0 1 0 1 0 1 0 0 0 0 0 0 0 1 1 1 1 0 1 1 1 0
 1 0 0 0 0]
[1 0 0 1 0 0 0 0 0 0 0 0 0 0 0 0 1 0 0 0 1 

 0 0 0 0 0]
[1 0 0 1 0 0 0 0 0 0 0 0 0 0 0 0 1 0 1 1 1 0 0 0 1 1 1 1 0 1 0 1 1 1 1 1 1
 1 0 0 1 0]
[1 1 0 1 0 1 0 0 0 0 0 0 0 0 0 0 1 0 1 0 1 0 0 0 0 0 0 0 0 1 0 1 0 0 1 1 0
 0 0 0 0 0]
[1 1 0 1 1 0 0 0 0 0 0 0 0 0 0 0 1 0 1 0 1 1 0 0 1 0 0 1 1 1 0 1 0 1 1 0 1
 1 1 1 0 0]
[1 0 0 1 0 0 0 0 0 0 0 0 0 0 0 0 1 0 1 0 1 0 1 0 1 1 0 1 0 1 1 1 0 1 1 1 1
 1 0 0 0 0]
[1 1 0 1 1 0 0 0 0 0 0 0 0 0 0 0 1 0 1 1 0 0 0 0 1 0 0 1 0 0 1 0 0 0 1 1 1
 1 0 0 0 0]
[1 0 0 1 0 0 0 0 0 0 0 0 0 0 0 0 1 0 1 1 0 1 0 0 1 1 0 0 0 1 1 1 0 1 1 1 1
 1 0 0 0 0]
[1 0 0 1 1 0 0 0 0 0 0 0 0 0 0 0 1 0 1 1 1 0 0 0 1 1 0 1 0 0 1 0 0 1 1 1 0
 1 0 0 1 0]
[1 0 0 1 0 0 0 0 0 0 0 0 0 0 0 0 1 0 1 0 1 0 0 1 1 1 0 1 1 0 0 1 1 1 1 1 1
 1 0 0 1 0]
[1 0 0 1 0 0 0 0 0 0 0 0 0 0 0 0 1 0 1 0 1 0 0 1 1 1 0 1 1 0 0 1 1 1 1 1 1
 1 0 0 1 0]
[1 0 0 1 0 0 0 0 0 0 0 0 0 0 0 0 1 1 1 0 0 0 1 0 1 1 0 0 1 1 1 0 0 0 1 0 0
 1 1 1 0 0]
[1 1 0 1 1 1 0 0 0 0 0 0 0 0 0 0 1 1 1 1 1 1 1 1 1 0 1 0 0 1 1 1 0 1 1 1 1
 1 0 0 0 0]
[1 0 0 1 0 0 0 0 0 0 0 0 0 0 0 

[1 0 0 1 1 0 0 0 0 0 0 0 0 0 0 0 1 1 1 0 1 0 0 1 1 1 0 1 1 0 1 1 0 1 1 1 0
 1 1 0 0 0]
[0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 1 0 1 0 0 0 0 0 1 1 0 0 0 0 0 1 0 1 1 1 0
 1 0 0 0 0]
[1 0 0 1 0 0 0 0 0 0 0 0 0 0 0 0 1 0 1 0 0 0 1 1 1 1 0 1 0 1 0 1 0 1 1 1 1
 1 0 0 0 0]
[1 0 0 1 0 0 0 0 0 0 0 0 0 0 0 0 1 0 1 1 1 0 0 0 1 1 0 1 0 1 1 1 0 1 1 0 0
 1 0 0 0 0]
[1 1 0 1 1 0 0 0 0 0 0 0 1 0 0 0 1 0 1 0 1 1 0 0 1 0 1 0 1 1 1 0 0 1 0 1 0
 0 1 0 1 0]
[1 1 0 1 0 0 0 0 0 0 0 0 0 0 0 0 1 0 1 1 0 0 0 0 1 0 0 0 1 0 1 0 0 0 0 0 1
 0 0 0 0 0]
[1 0 0 1 1 0 0 0 0 0 0 0 0 0 0 0 1 1 1 1 1 0 1 0 1 1 0 1 0 1 1 1 1 1 1 1 1
 1 0 0 1 0]
[1 0 0 1 0 0 0 0 0 0 0 0 0 0 0 0 1 1 1 1 1 0 1 1 1 1 1 1 1 1 1 0 0 1 0 1 1
 1 0 0 0 0]
[1 0 0 1 1 0 0 0 0 0 0 0 0 0 0 0 1 0 1 0 1 0 0 0 1 1 0 0 0 0 0 1 0 1 0 1 0
 1 0 0 0 0]
[1 0 0 1 0 0 0 0 1 0 1 0 0 0 0 0 1 1 0 0 0 0 1 0 1 1 1 1 0 0 1 0 0 0 0 1 1
 1 0 0 0 0]
[1 0 0 1 1 0 0 0 0 0 0 0 0 0 1 0 1 1 1 0 1 0 1 0 1 1 1 1 1 1 1 1 0 1 1 1 0
 1 1 0 0 0]
[1 0 0 1 0 0 0 0 0 0 0 0 0 0 0 0 1 0 1 0 1 

 0 1 0 0 0]
[1 1 0 1 0 1 0 0 0 0 0 0 0 0 0 0 0 0 1 0 1 1 0 0 1 0 0 1 1 1 1 0 0 1 1 1 0
 0 0 0 1 0]
[1 0 0 1 0 0 0 0 0 0 0 0 0 0 0 0 1 0 0 1 1 0 0 0 1 1 0 1 0 1 1 0 0 1 1 1 0
 1 1 0 0 0]
[1 0 0 1 0 0 0 0 0 0 0 0 0 0 0 0 1 0 1 1 1 0 1 1 1 1 0 1 1 1 1 1 0 1 1 1 1
 1 0 0 0 0]
[0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 1 0 1 0 0 0 0 0 1 1 0 0 0 0 0 1 0 1 1 1 0
 1 0 0 0 0]
[1 1 0 1 1 0 0 0 0 0 0 0 0 0 0 0 1 1 1 1 1 0 0 0 1 0 0 1 1 1 1 0 0 1 1 1 1
 0 0 1 1 0]
[1 1 0 1 1 1 0 0 0 0 0 0 0 0 0 0 1 0 1 1 1 0 0 0 1 0 0 1 1 1 1 0 0 0 1 1 1
 1 0 0 0 0]
[1 0 0 1 1 0 0 0 0 0 0 0 0 0 0 0 1 1 1 0 1 0 0 0 1 1 0 0 0 0 1 1 0 1 1 1 0
 1 1 0 0 0]
[0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 1 0 1 0 0 0 0 0 1 1 0 0 0 0 0 1 0 1 1 1 0
 1 0 0 0 0]
[1 0 0 1 0 0 0 0 0 0 0 0 0 0 0 0 1 0 1 0 1 0 0 1 1 1 0 1 1 0 0 1 1 1 1 1 1
 1 0 0 1 0]
[1 0 0 1 1 0 0 0 0 1 0 0 0 0 0 0 1 0 1 0 1 0 1 0 1 1 0 1 1 0 1 1 0 1 1 1 0
 1 0 0 0 0]
[1 0 0 1 1 0 0 0 0 0 0 0 0 0 0 0 1 1 1 0 1 0 0 0 1 1 0 0 0 0 1 1 0 1 1 1 0
 1 1 0 0 0]
[1 0 0 1 0 0 0 0 0 0 0 0 0 0 0 

[0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 1 0 0 0 0 0 0 0 0 1 0 0 0 0 0 0 0 0 0 0 0
 1 0 0 0 0]
[1 0 0 1 0 1 0 0 0 0 0 0 0 0 0 0 1 0 0 0 1 0 0 0 1 1 0 0 1 1 0 0 0 0 1 1 0
 1 0 0 1 0]
[1 0 0 1 0 0 0 0 0 0 0 0 0 0 0 0 1 0 1 0 1 0 1 1 1 1 0 1 1 0 0 1 0 1 1 1 0
 1 0 1 0 0]
[1 0 0 1 1 0 0 0 0 1 0 0 0 0 0 0 1 0 1 0 1 0 0 0 1 1 0 1 0 1 1 1 0 1 1 1 0
 1 0 0 1 0]
[1 0 0 1 0 0 0 0 0 0 0 0 0 0 0 0 1 0 1 0 1 0 0 0 1 1 0 0 0 0 0 1 1 1 1 1 1
 1 0 0 1 0]
[0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 1 0 0 0 0 0 0 0 0 1 0 0 0 0 0 0 0 0 0 0 0
 1 0 0 0 0]
[1 1 0 1 0 0 0 0 0 0 0 0 0 0 0 0 1 0 1 0 0 0 0 1 0 0 0 0 1 0 0 0 0 1 1 1 0
 0 0 0 0 0]
[1 0 0 1 1 0 0 0 0 0 0 0 0 0 0 0 1 1 1 0 1 0 1 0 1 1 1 1 1 1 1 1 0 1 1 1 1
 1 0 0 1 0]
[1 1 0 1 0 0 0 0 0 0 0 0 0 0 0 0 1 0 1 0 1 1 1 0 1 0 0 0 1 1 1 1 0 0 0 1 1
 0 1 1 0 0]
[1 1 0 1 0 0 0 0 0 0 0 0 0 0 0 0 1 0 1 1 0 1 1 0 1 0 0 1 1 0 0 1 0 1 0 1 0
 0 1 1 0 0]
[1 0 0 1 1 0 0 0 0 0 0 0 0 0 0 0 1 0 1 1 1 1 0 0 1 1 1 0 0 1 1 1 0 1 1 1 0
 1 0 1 0 0]
[1 0 0 1 0 0 0 0 0 0 0 0 0 0 0 0 1 0 1 0 1 

# NeW

In [95]:
all_tags = [item for sublist in final_df_list[3].values for item in sublist]
freq = nltk.FreqDist(all_tags)

frequent_tags = freq.most_common(100)

freq_tag = []
for tag in frequent_tags:
    freq_tag.append(tag[0])

In [96]:
freq_tag

['javascript',
 'java',
 'c#',
 ' jquery',
 ' html',
 ' android',
 ' angularjs',
 ' css',
 ' asp.net',
 ' php',
 ' json',
 ' arrays',
 ' ajax',
 ' .net',
 ' node.js',
 ' spring',
 ' asp.net-mvc',
 ' wpf',
 ' swing',
 ' xml',
 ' regex',
 ' linq',
 ' html5',
 ' mysql',
 ' multithreading',
 ' entity-framework',
 ' hibernate',
 ' eclipse',
 ' winforms',
 ' string',
 ' sql',
 ' twitter-bootstrap',
 ' maven',
 ' xaml',
 ' spring-mvc',
 ' jsp',
 ' sql-server',
 ' reactjs',
 ' forms',
 ' d3.js',
 ' generics',
 ' arraylist',
 ' mongodb',
 ' object',
 ' google-maps',
 ' rest',
 ' web-services',
 ' asp.net-mvc-4',
 ' jpa',
 ' selenium',
 ' c#',
 ' image',
 ' google-chrome',
 ' canvas',
 ' sockets',
 ' asynchronous',
 ' servlets',
 ' unit-testing',
 ' ruby-on-rails',
 ' list',
 ' jdbc',
 ' express',
 ' validation',
 ' loops',
 ' unity3d',
 ' sorting',
 ' function',
 ' tomcat',
 ' database',
 ' excel',
 ' class',
 ' visual-studio',
 ' meteor',
 ' date',
 ' javafx',
 ' performance',
 ' dom',
 ' meth

In [97]:
def most_frequent(t, frequent):
    
    tags = []
    for i in range(len(t)):
        if t[i] in frequent:
            tags.append(t[i])
    return tags

In [86]:
frequent_df = full.copy()
print(frequent_df)
frequent_df['Tag'] = frequent_df['Tag'].apply(lambda x: str(x).split(','))
# frequent_df

                                                    Title  \
0                   db viewmodel data displaying mvc view   
1                                    decrypt pixel bitmap   
2       using http load angular j json file working fi...   
3       location provided redundantly two different pl...   
4                using ajaxform plugin view ajax response   
5          add column search filter jqgrid severside code   
6                serversocket communication client socket   
7                           understand use gridlayoutspec   
8               unknown error rest application deployment   
9       change color next line drawing without closing...   
10      need best combination array element specific s...   
11                           iterate item arraylist index   
12                            casperjs submit form action   
13                new java understanding java compilation   
14      create single entity existing entity using que...   
15                      

In [99]:
frequent_df = full.copy()

In [100]:
frequent_df['Tag'] = frequent_df['Tag'].apply(lambda x: most_frequent(x, freq_tag))
frequent_df['Tag'] = frequent_df['Tag'].apply(lambda x: x if len(x)>0 else None)

In [103]:
# Drop nan values from the dataset
new_preprocess = frequent_df.dropna(subset=['Tag', 'Title'], inplace=False)
dataframe = new_preprocess.dropna(subset=['Title'], inplace=False)

In [105]:
multilabel_binarizer_title = MultiLabelBinarizer()
y_bin_title = multilabel_binarizer_title.fit_transform(dataframe['Tag'].values)
y_bin_title.shape

(156420, 100)

In [106]:
X_train_title, X_test_title, y_train_title, y_test_title = train_test_split(dataframe['Title'].values, y_bin_title, test_size = 0.3, random_state = 0)

In [107]:
X_train_title_tfidf, tfidf_title = calculate_tfidf_vector(X_train_title.ravel())
X_test_title_tfidf = tfidf_title.transform(X_test_title.ravel())

In [108]:
mn_accuracy_title, mn_y_pred_title, mn_clf_title = apply_model(mn, X_train_title_tfidf, y_train_title, X_test_title_tfidf, y_test_title)
print(mn_accuracy_title)

0.2332608788304991


In [109]:
mn_title_accuracy, mn_title_recall, mn_title_precision, mn_title_f1, mn_title_hamming, mn_title_jaccard = evaluation_metrics(y_test_title, mn_y_pred_title)

Accuracy: 0.2332608788304991
Recall: 0.3985615911288254
Precision: 0.9005974408132329
F1-Score: 0.5525783066611955
Hamming Loss: 0.013941524954183182
Jaccard Similarity Score: 0.4559613616575642


In [110]:
svc = LinearSVC()
svc_accuracy_title, svc_y_pred_title, svc_clf_title = apply_model(svc, X_train_title_tfidf, y_train_title, X_test_title_tfidf, y_test_title)
print(svc_accuracy_title)

0.3705621617014022


In [111]:
svc_title_accuracy, svc_title_recall, svc_title_precision, svc_title_f1, svc_title_hamming, svc_title_jaccard = evaluation_metrics(y_test_title, svc_y_pred_title)

Accuracy: 0.3705621617014022
Recall: 0.5973836348927606
Precision: 0.8530613394945198
F1-Score: 0.7026876479598942
Hamming Loss: 0.010919319780079274
Jaccard Similarity Score: 0.6032370368340831


In [ ]:
c=0
for j in range (len(y_test_title)):
    count=0
    for k in range (len(y_test_title[j])):
        if(mn_y_pred[j][k]==y_test_title[j][k]==1):
            count=count+1
    if(count>1):
        c=c+1
print(c)
print(c/len(svc_y_pred))

In [152]:
import gc
gc.collect()

2984

# NEW BODY PART

In [112]:
multilabel_binarizer_body = MultiLabelBinarizer()
y_bin_body = multilabel_binarizer_body.fit_transform(dataframe['Tag'].values)

In [113]:
X_train_body, X_test_body, y_train_body, y_test_body = train_test_split(dataframe['Body'].values, y_bin_body, test_size = 0.3, random_state = 0)

In [114]:
X_train_body_tfidf, tfidf_body = calculate_tfidf_vector(X_train_body.ravel())
X_test_body_tfidf = tfidf_body.transform(X_test_body.ravel())

In [115]:
mn_accuracy_body, mn_y_pred_body, mn_clf_body = apply_model(mn, X_train_body_tfidf, y_train_body, X_test_body_tfidf, y_test_body)
print(mn_accuracy_body)

0.19611729105399991


In [116]:
mn_body_accuracy, mn_body_recall, mn_body_precision, mn_body_f1, mn_body_hamming, mn_body_jaccard = evaluation_metrics(y_test_body, mn_y_pred_body)

Accuracy: 0.19611729105399991
Recall: 0.3686194037213157
Precision: 0.8827253827253827
F1-Score: 0.5200640267241979
Hamming Loss: 0.014695904189575075
Jaccard Similarity Score: 0.41105344686568307


In [117]:
svc = LinearSVC()
svc_accuracy_body, svc_y_pred_body, svc_clf_body = apply_model(svc, X_train_body_tfidf, y_train_body, X_test_body_tfidf, y_test_body)
print(svc_accuracy_body)

0.3403230618420492


In [118]:
svc_body_accuracy, svc_body_recall, svc_body_precision, svc_body_f1, svc_body_hamming, svc_body_jaccard = evaluation_metrics(y_test_body, svc_y_pred_body)

Accuracy: 0.3403230618420492
Recall: 0.5879915550206192
Precision: 0.8349677780891006
F1-Score: 0.6900464276203818
Hamming Loss: 0.01140987938456293
Jaccard Similarity Score: 0.5871446786531175


# NEW TITLE & BODY COMBINED

In [119]:
X_train_title_body, X_test_title_body, y_train_title_body, y_test_title_body = train_test_split(dataframe[['Title', 'Body']], y_bin_body, test_size = 0.3, random_state = 0)

In [120]:
y_train_title_body.shape

(109494, 100)

In [121]:
import numpy as np
from scipy.sparse import coo_matrix, hstack
X_train_title_body_tfidf1, tfidf_title_body1 = calculate_tfidf_vector(X_train_title_body['Title'].ravel())
X_test_title_body_tfidf1 = tfidf_title_body1.transform(X_test_title_body['Title'].ravel())


X_train_title_body_tfidf2, tfidf_title_body2 = calculate_tfidf_vector(X_train_title_body['Body'].ravel())
X_test_title_body_tfidf2 = tfidf_title_body2.transform(X_test_title_body['Body'].ravel())

X_train_tfidf_combined = hstack([X_train_title_body_tfidf1, X_train_title_body_tfidf2])
X_test_tfidf_combined = hstack([X_test_title_body_tfidf1, X_test_title_body_tfidf2])

In [122]:
y_train_title_body.shape

(109494, 100)

In [123]:
mn_accuracy_tb, mn_y_pred_tb, clf_mn_tb = apply_model(mn, X_train_tfidf_combined, y_train_title_body, X_test_tfidf_combined, y_test_title_body)
print(mn_accuracy_tb)

0.29390955973234456


In [124]:
mn_tb_accuracy, mn_tb_recall, mn_tb_precision, mn_tb_f1, mn_tb_hamming, mn_tb_jaccard = evaluation_metrics(y_test_title_body, mn_y_pred_tb)

Accuracy: 0.29390955973234456
Recall: 0.5229079931335214
Precision: 0.8478445173158442
F1-Score: 0.646863196177621
Hamming Loss: 0.012332395686826066
Jaccard Similarity Score: 0.5505353863827843


In [125]:
svc = LinearSVC()
svc_accuracy_tb, svc_y_pred_tb, clf_svc_tb = apply_model(svc, X_train_tfidf_combined, y_train_title_body, X_test_tfidf_combined, y_test_title_body)
print(svc_accuracy_tb)


0.40757788859054683


In [127]:
accuracy_score(y_test_title_body, svc_y_pred_tb)

0.40757788859054683

In [128]:
svc_tb_accuracy, svc_tb_recall, svc_tb_precision, svc_tb_f1, svc_tb_hamming, svc_tb_jaccard = evaluation_metrics(y_test_title_body, svc_y_pred_tb)

Accuracy: 0.40757788859054683
Recall: 0.6765553165880704
Precision: 0.847477106736366
F1-Score: 0.7524316851454621
Hamming Loss: 0.00961663043941525
Jaccard Similarity Score: 0.6650300726777519


# Merged Voting

In [129]:
svc_y_pred_code

array([[0, 0, 0],
       [0, 1, 0],
       [1, 1, 0],
       ...,
       [0, 1, 0],
       [0, 0, 1],
       [1, 0, 0]])

In [132]:
code_classes = multilabel_binarizer.classes_
tb_classes = multilabel_binarizer_body.classes_



In [135]:
new_predictions =  np.copy(svc_y_pred_tb)
tb = tb_classes.tolist()
for i in range(code_classes.shape[0]):
    ls = []
    lan = code_classes[i]
    ind = tb.index(lan)
    tb1 = svc_y_pred_tb[:, ind]
    code1 = svc_y_pred_code[:, i]
    for j in range(tb1.shape[0]):
        if code1[j] == 1 and tb1[j] == 0:
            new_predictions[j][i] = 1


In [136]:
from sklearn.metrics import accuracy_score
accuracy_score(y_test_title_body, new_predictions)

0.37897967011891065

In [137]:
combined_accuracy, combined_recall, combined_precision, combined_f1, combined_hamming, combined_jaccard = evaluation_metrics(y_test_title_body, new_predictions)

Accuracy: 0.37897967011891065
Recall: 0.6780548923659754
Precision: 0.7826210728885549
F1-Score: 0.7265951654764484
Hamming Loss: 0.011022247794399693
Jaccard Similarity Score: 0.6481120900248889


# NEW TITLE AND CODE PART

In [139]:
da = dataframe[['Title']]
final_df_list = final_df_list[[0]]
dfs = pd.DataFrame()
dfs = pd.concat([dfs, da, final_df_list], axis=1, ignore_index=True).reset_index(drop=True)

In [141]:
X_train_title_code, X_test_title_code, y_train_title_code, y_test_title_code = train_test_split(dfs[[0, 1]], y_bin_body, test_size = 0.3, random_state = 0)

In [146]:
X_train_title_code

0  \
103861                                       cant run app   
140456  retaining count value dynamically adding text ...   
123053  getting severe messagebodywriter found medium ...   
122290                     knockout kogrid data displayed   
5768    make saveframe method extractmpegframestest ef...   
75463   use cookiejs load page differently based previ...   
12207                       webservice client java jaxrpc   
52209                         angular translate ui router   
45676    gracefully close tcplistenertcpclient connection   
143328                    bookmark current page ie chrome   
112347                    sequelizejs passing array value   
47621                  way skip first node using iterator   
88649                        parse html table json jquery   
103170  vertical multilevel accordion menu documentget...   
141785        resolving different main file per directory   
120924  move multiple jslider according assigned jtext...   
68761         angular facebook service hit api call limit   
27886   meteorjs external mongo meteor cannot login mongo   
87259   testing disk performance differs without using...   
44599   create array userprovided number map array num...   
35297           javascript calling function onclick event   
100418                        using promise event emitter   
37611   edit one instance variable value others anothe...   
131692  combine touch mouse event handler without prod...   
26579   convert text file treestructured content relat...   
80090              make bootstrap carousel scale properly   
106988  google map api geocoder getfromlocationname re...   
69475               using thread local sdf removing usage   
15133   jquery ajax formserialize working server local ii   
126441     adding working time slider javafx video player   
...                                                   ...   
49811          simple exception handling nested java apis   
131869      correctly implement jquery multiselect widget   
31921              android exporting event local calendar   
108504             open new window tab keep focus current   
155747    validate user input accept type int string quit   
133568              java mysql communication link failure   
73135   bootstrap responsive navbar showing collapsed ...   
132943                    jquery getjson plain javascript   
83966                change text label eclipse using java   
7877          copy row one table another using javascript   
70608   way call parent class method child class objec...   
67699                           radio button datatemplate   
137993                    jquery return native dom object   
82457          fullcalendar eventmouseover rerenderevents   
101201                  find spark installation directory   
108631             increase maximum byte size nodejs pipe   
150055                  swift concept character type java   
17089   rendering nonnull render tarhet xna disables a...   
80186   custom validation attribute check duplicate am...   
52620   user input string nothing happens upon pressin...   
48600                           complex sinatra parameter   
112420                        progress process website c#   
86293                              associativity math c c   
122579  show name input box name number dropdown list ...   
41993                                  aspectj annotation   
97639   cannot add new givenwhenthen getting error syn...   
95939                     lock item search result android   
152315                                 cs spring security   
117952       c# code set cursor position outlook mailitem   
43567   search first sorted integer unsorted array length   

                                                        1  
103861  public class Add extends Activity {\n@Override...  
140456  public class Book\n{\n    public string Title ...  
123053    private void testUpdateUser(){\n      FormBe...  
122290  public class AdminViewMod

In [147]:
X_train_title_code_tfidf1, tfidf_title_code1 = calculate_tfidf_vector(X_train_title_code[0].ravel())
X_test_title_code_tfidf1 = tfidf_title_code1.transform(X_test_title_body['Title'].ravel())

X_train_title_code_tfidf2, tfidf_title_code2 = calculate_tfidf_vector(X_train_title_code[1].ravel())
X_test_title_code_tfidf2 = tfidf_title_code2.transform(X_test_title_code[1].ravel())

X_train_tfidf_combined_tc = hstack([X_train_title_code_tfidf1, X_train_title_code_tfidf2])
X_test_tfidf_combined_tc = hstack([X_test_title_code_tfidf1, X_test_title_code_tfidf2])

In [148]:
mn_accuracy_tc, mn_y_pred_tc, clf_mn_tc = apply_model(mn, X_train_tfidf_combined_tc, y_train_title_code, X_test_tfidf_combined_tc, y_test_title_code)
print(mn_accuracy_tb)

0.29390955973234456


In [149]:
mn_tc_accuracy, mn_tc_recall, mn_tc_precision, mn_tc_f1, mn_tc_hamming, mn_tc_jaccard = evaluation_metrics(y_test_title_code, mn_y_pred_tc)

Accuracy: 0.33013681114946936
Recall: 0.6217813381740692
Precision: 0.8090500641848524
F1-Score: 0.7031607367986522
Hamming Loss: 0.011339555896517922
Jaccard Similarity Score: 0.6146236535150295


In [150]:
svc = LinearSVC()
svc_accuracy_tc, svc_y_pred_tc, clf_svc_tc = apply_model(svc, X_train_tfidf_combined_tc, y_train_title_code, X_test_tfidf_combined_tc, y_test_title_code)
print(svc_accuracy_tc)


0.41678387248007503


In [151]:
svc_tc_accuracy, svc_tc_recall, svc_tc_precision, svc_tc_f1, svc_tc_hamming, svc_tc_jaccard = evaluation_metrics(y_test_title_code, svc_y_pred_tc)

Accuracy: 0.41678387248007503
Recall: 0.6865097373769262
Precision: 0.8581223563650714
F1-Score: 0.7627827440491523
Hamming Loss: 0.009223245109321059
Jaccard Similarity Score: 0.6820273510674355


In [ ]:
# mnb_only_title_precision  = []
# svc_only_title_precision = []
# mnb_only_body_precision = []
# svc_only_body_precision = []
# mnb_title_body_precision = []

In [ ]:
# X = np.arange(5)
# plt.bar(X + 0.00, data[0], color = 'b', width = 0.25)
# plt.bar(X + 0.25, data[1], color = 'g', width = 0.25)
# plt.bar(X + 0.50, data[2], color = 'r', width = 0.25)